In [1]:
import polars as pl
import altair as alt
from vega_datasets import data

alt.theme.enable('latimes')

alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

## load airport data

In [18]:
#file = 'https://davidmegginson.github.io/ourairports-data/airports.csv'
file = 'https://github.com/usefulmove/code/raw/refs/heads/main/eda/airports/airports.parquet'

airports = pl.read_parquet(file)

airports.sample(8)

shape: (8, 19)
┌────────┬─────────┬────────────┬────────────┬───┬────────────┬───────────┬────────────┬───────────┐
│ id     ┆ ident   ┆ type       ┆ name       ┆ … ┆ local_code ┆ home_link ┆ wikipedia_ ┆ keywords  │
│ ---    ┆ ---     ┆ ---        ┆ ---        ┆   ┆ ---        ┆ ---       ┆ link       ┆ ---       │
│ i64    ┆ str     ┆ str        ┆ str        ┆   ┆ str        ┆ str       ┆ ---        ┆ str       │
│        ┆         ┆            ┆            ┆   ┆            ┆           ┆ str        ┆           │
╞════════╪═════════╪════════════╪════════════╪═══╪════════════╪═══════════╪════════════╪═══════════╡
│ 1467   ┆ CPW2    ┆ heliport   ┆ London     ┆ … ┆ CPW2       ┆ null      ┆ null       ┆ PW2       │
│        ┆         ┆            ┆ (Victoria  ┆   ┆            ┆           ┆            ┆           │
│        ┆         ┆            ┆ Hospital)  ┆   ┆            ┆           ┆            ┆           │
│        ┆         ┆            ┆ Hel…       ┆   ┆            ┆           ┆            ┆           │
│ 342025 ┆ VU-0004 ┆ closed     ┆ Luganville ┆ … ┆ null       ┆ null      ┆ https://en ┆ null      │
│        ┆         ┆            ┆ Seaplane   ┆   ┆            ┆           ┆ .wikipedia ┆           │
│        ┆         ┆            ┆ Base       ┆   ┆            ┆           ┆ .org/wiki/ ┆           │
│        ┆         ┆            ┆            ┆   ┆            ┆           ┆ …          ┆           │
│ 349551 ┆ PH-0432 ┆ small_airp ┆ Sagpangan  ┆ … ┆ null       ┆ null      ┆ null       ┆ null      │
│        ┆         ┆ ort        ┆ Airport    ┆   ┆            ┆           ┆            ┆           │
│ 5263   ┆ OPMR    ┆ medium_air ┆ Masroor    ┆ … ┆ null       ┆ null      ┆ https://en ┆ null      │
│        ┆         ┆ port       ┆ Air Base   ┆   ┆            ┆           ┆ .wikipedia ┆           │
│        ┆         ┆            ┆            ┆   ┆            ┆           ┆ .org/wiki/ ┆           │
│        ┆         ┆            ┆            ┆   ┆            ┆           ┆ …          ┆           │
│ 12014  ┆ 54NJ    ┆ seaplane_b ┆ Highlands  ┆ … ┆ 54NJ       ┆ null      ┆ null       ┆ null      │
│        ┆         ┆ ase        ┆ Seaplane   ┆   ┆            ┆           ┆            ┆           │
│        ┆         ┆            ┆ Base       ┆   ┆            ┆           ┆            ┆           │
│ 325784 ┆ LV-0017 ┆ small_airp ┆ Mežāre     ┆ … ┆ null       ┆ null      ┆ null       ┆ null      │
│        ┆         ┆ ort        ┆ Airstrip   ┆   ┆            ┆           ┆            ┆           │
│ 11172  ┆ 46NE    ┆ small_airp ┆ Jantzen    ┆ … ┆ 46NE       ┆ null      ┆ null       ┆ null      │
│        ┆         ┆ ort        ┆ Airport    ┆   ┆            ┆           ┆            ┆           │
│ 595288 ┆ AU-0754 ┆ small_airp ┆ Lynton     ┆ … ┆ null       ┆ null      ┆ null       ┆ Lynton    │
│        ┆         ┆ ort        ┆ Airfield   ┆   ┆            ┆           ┆            ┆ Station   │
└────────┴─────────┴────────────┴────────────┴───┴────────────┴───────────┴────────────┴───────────┘

In [19]:
airports_us = airports.filter(
    pl.col('iso_country') == 'US',
    pl.col('type') != 'closed',
)

display(airports_us.shape)

display(airports_us.group_by('type').agg(pl.col('type').len().alias('count')))

(25015, 19)

shape: (6, 2)
┌────────────────┬───────┐
│ type           ┆ count │
│ ---            ┆ ---   │
│ str            ┆ u32   │
╞════════════════╪═══════╡
│ small_airport  ┆ 15250 │
│ large_airport  ┆ 71    │
│ medium_airport ┆ 832   │
│ balloonport    ┆ 29    │
│ seaplane_base  ┆ 659   │
│ heliport       ┆ 8174  │
└────────────────┴───────┘

## u.s. airport locations

In [30]:
fig_width, fig_height = 1300, 900

# read in polygons from topojson
states = alt.topo_feature(data.us_10m.url, feature='states')

# US states background
states_background = alt.Chart(
    states,
    title='u.s. airports',
).mark_geoshape(
    fill='#faf6e4',
    stroke='#ff991c',
    strokeWidth=0.5,
).properties(
    width=fig_width,
    height=fig_height,
).project('albersUsa')

airports_chart = alt.Chart(
    airports_us.filter(
        pl.col('type').str.contains('airport'),
    ).with_columns(
        pl.when(pl.col('type') == 'large_airport').then(3)
            .when(pl.col('type') == 'medium_airport').then(2)
            .when(pl.col('type') == 'small_airport').then(1)
            .otherwise(0)
        .alias('airport_size'),
        pl.col('type').str.replace('_', ' '),
    ),
).mark_circle().encode(
    latitude='latitude_deg:Q',
    longitude='longitude_deg:Q',
    size=alt.Size(
        'type:O',
        title='',
        sort=alt.SortField(field='airport_size', order='ascending'),
        scale=alt.Scale(
            domain=['small airport', 'medium airport', 'large airport'],
            range=[10, 300],
        ),
    ),
    opacity=alt.Opacity(
        'type:O',
        scale=alt.Scale(
            domain=['medium airport', 'large airport', 'small airport'],
            range=[0.5, 1.0],
        ),
        legend=None,
    ),
    color=alt.Color(
        'type:N',
        title='',
        scale=alt.Scale(
            domain=['small airport', 'medium airport', 'large airport'],
            range=['#ef9d6e', '#ef9d6e', '#0060ff'],
        ),
    ),
    tooltip='custom_tooltip:N',
).transform_calculate(
    custom_tooltip='datum.name + " - " + datum.ident + " - " + datum.municipality',
).project(
    type='albersUsa',
).properties(
    width=fig_width,
    height=fig_height,
)

(states_background + airports_chart).show()

#(states_background + airports_chart).save('airports.html')

alt.LayerChart(...)

## load flight data

In [7]:
flights = pl.read_csv(data.flights_airport.base_url + data.flights_airport.filename)

print(flights.shape)

display(flights.sample(4))

(5366, 3)


shape: (4, 3)
┌────────┬─────────────┬───────┐
│ origin ┆ destination ┆ count │
│ ---    ┆ ---         ┆ ---   │
│ str    ┆ str         ┆ i64   │
╞════════╪═════════════╪═══════╡
│ CAE    ┆ ORD         ┆ 1696  │
│ LAX    ┆ TPA         ┆ 516   │
│ JFK    ┆ IND         ┆ 125   │
│ DEN    ┆ BHM         ┆ 651   │
└────────┴─────────────┴───────┘

In [8]:
flights_info_us = flights.join(
    airports,
    left_on='origin',
    right_on='iata_code',
    how='left',
).select(
    pl.col('origin'),
    pl.col('type').alias('origin_type'),
    pl.col('name').alias('origin_name'),
    pl.col('latitude_deg').alias('origin_latitude'),
    pl.col('longitude_deg').alias('origin_longitude'),
    pl.col('elevation_ft').alias('origin_elevation'),
    pl.col('continent').alias('origin_continent'),
    pl.col('iso_country').alias('origin_country'),
    pl.col('iso_region').alias('origin_region'),
    pl.col('municipality').alias('origin_municipality'),
    pl.col('destination'),
    pl.col('count').alias('flights'),
).join(
    airports,
    left_on='destination',
    right_on='iata_code',
    how='left',
).select(
    pl.col('origin'),
    pl.col('origin_type'),
    pl.col('origin_name'),
    pl.col('origin_latitude'),
    pl.col('origin_longitude'),
    pl.col('origin_elevation'),
    pl.col('origin_continent'),
    pl.col('origin_country'),
    pl.col('origin_region'),
    pl.col('origin_municipality'),
    pl.col('destination'),
    pl.col('type').alias('dest_type'),
    pl.col('name').alias('dest_name'),
    pl.col('latitude_deg').alias('dest_latitude'),
    pl.col('longitude_deg').alias('dest_longitude'),
    pl.col('elevation_ft').alias('dest_elevation'),
    pl.col('continent').alias('dest_continent'),
    pl.col('iso_country').alias('dest_country'),
    pl.col('iso_region').alias('dest_region'),
    pl.col('municipality').alias('dest_municipality'),
    pl.col('flights'),
).filter(
    (pl.col('origin_country') == 'US') & (pl.col('dest_country') == 'US'),
)

flights_info_us.head(10)

shape: (10, 21)
┌────────┬────────────┬────────────┬────────────┬───┬────────────┬───────────┬───────────┬─────────┐
│ origin ┆ origin_typ ┆ origin_nam ┆ origin_lat ┆ … ┆ dest_count ┆ dest_regi ┆ dest_muni ┆ flights │
│ ---    ┆ e          ┆ e          ┆ itude      ┆   ┆ ry         ┆ on        ┆ cipality  ┆ ---     │
│ str    ┆ ---        ┆ ---        ┆ ---        ┆   ┆ ---        ┆ ---       ┆ ---       ┆ i64     │
│        ┆ str        ┆ str        ┆ f64        ┆   ┆ str        ┆ str       ┆ str       ┆         │
╞════════╪════════════╪════════════╪════════════╪═══╪════════════╪═══════════╪═══════════╪═════════╡
│ ABE    ┆ medium_air ┆ Lehigh     ┆ 40.651773  ┆ … ┆ US         ┆ US-GA     ┆ Atlanta   ┆ 853     │
│        ┆ port       ┆ Valley Int ┆            ┆   ┆            ┆           ┆           ┆         │
│        ┆            ┆ ernational ┆            ┆   ┆            ┆           ┆           ┆         │
│        ┆            ┆ Ai…        ┆            ┆   ┆            ┆           ┆           ┆         │
│ ABE    ┆ medium_air ┆ Lehigh     ┆ 40.651773  ┆ … ┆ US         ┆ US-AL     ┆ Birmingha ┆ 1       │
│        ┆ port       ┆ Valley Int ┆            ┆   ┆            ┆           ┆ m         ┆         │
│        ┆            ┆ ernational ┆            ┆   ┆            ┆           ┆           ┆         │
│        ┆            ┆ Ai…        ┆            ┆   ┆            ┆           ┆           ┆         │
│ ABE    ┆ medium_air ┆ Lehigh     ┆ 40.651773  ┆ … ┆ US         ┆ US-OH     ┆ Cleveland ┆ 805     │
│        ┆ port       ┆ Valley Int ┆            ┆   ┆            ┆           ┆           ┆         │
│        ┆            ┆ ernational ┆            ┆   ┆            ┆           ┆           ┆         │
│        ┆            ┆ Ai…        ┆            ┆   ┆            ┆           ┆           ┆         │
│ ABE    ┆ medium_air ┆ Lehigh     ┆ 40.651773  ┆ … ┆ US         ┆ US-NC     ┆ Charlotte ┆ 465     │
│        ┆ port       ┆ Valley Int ┆            ┆   ┆            ┆           ┆           ┆         │
│        ┆            ┆ ernational ┆            ┆   ┆            ┆           ┆           ┆         │
│        ┆            ┆ Ai…        ┆            ┆   ┆            ┆           ┆           ┆         │
│ ABE    ┆ medium_air ┆ Lehigh     ┆ 40.651773  ┆ … ┆ US         ┆ US-KY     ┆ Cincinnat ┆ 247     │
│        ┆ port       ┆ Valley Int ┆            ┆   ┆            ┆           ┆ i /       ┆         │
│        ┆            ┆ ernational ┆            ┆   ┆            ┆           ┆ Covington ┆         │
│        ┆            ┆ Ai…        ┆            ┆   ┆            ┆           ┆           ┆         │
│ ABE    ┆ medium_air ┆ Lehigh     ┆ 40.651773  ┆ … ┆ US         ┆ US-MI     ┆ Detroit   ┆ 997     │
│        ┆ port       ┆ Valley Int ┆            ┆   ┆            ┆           ┆           ┆         │
│        ┆            ┆ ernational ┆            ┆   ┆            ┆           ┆           ┆         │
│        ┆            ┆ Ai…        ┆            ┆   ┆            ┆           ┆           ┆         │
│ ABE    ┆ medium_air ┆ Lehigh     ┆ 40.651773  ┆ … ┆ US         ┆ US-NY     ┆ New York  ┆ 3       │
│        ┆ port       ┆ Valley Int ┆            ┆   ┆            ┆           ┆           ┆         │
│        ┆            ┆ ernational ┆            ┆   ┆            ┆           ┆           ┆         │
│        ┆            ┆ Ai…        ┆            ┆   ┆            ┆           ┆           ┆         │
│ ABE    ┆ medium_air ┆ Lehigh     ┆ 40.651773  ┆ … ┆ US         ┆ US-NY     ┆ New York  ┆ 9       │
│        ┆ port       ┆ Valley Int ┆            ┆   ┆            ┆           ┆           ┆         │
│        ┆            ┆ ernational ┆            ┆   ┆            ┆           ┆           ┆         │
│        ┆            ┆ Ai…        ┆            ┆   ┆            ┆           ┆           ┆         │
│ ABE    ┆ medium_air ┆ Lehigh     ┆ 40.651773  ┆ … ┆ US         ┆ US-IL     ┆ Chicago   ┆ 1425    │
│        ┆ port       ┆ Valley Int ┆         

## most frequent flights

In [9]:
flights_info_us.sort('flights', descending=True).select(
    pl.col('origin'),
    pl.col('origin_name'),
    pl.col('origin_municipality'),
    pl.col('destination'),
    pl.col('dest_name'),
    pl.col('dest_municipality'),
    pl.col('flights'),
).head(10)

shape: (10, 7)
┌────────┬────────────────┬────────────────┬─────────────┬───────────────┬───────────────┬─────────┐
│ origin ┆ origin_name    ┆ origin_municip ┆ destination ┆ dest_name     ┆ dest_municipa ┆ flights │
│ ---    ┆ ---            ┆ ality          ┆ ---         ┆ ---           ┆ lity          ┆ ---     │
│ str    ┆ str            ┆ ---            ┆ str         ┆ str           ┆ ---           ┆ i64     │
│        ┆                ┆ str            ┆             ┆               ┆ str           ┆         │
╞════════╪════════════════╪════════════════╪═════════════╪═══════════════╪═══════════════╪═════════╡
│ SFO    ┆ San Francisco  ┆ San Francisco  ┆ LAX         ┆ Los Angeles   ┆ Los Angeles   ┆ 13788   │
│        ┆ International  ┆                ┆             ┆ International ┆               ┆         │
│        ┆ Ai…            ┆                ┆             ┆ Airp…         ┆               ┆         │
│ LAX    ┆ Los Angeles    ┆ Los Angeles    ┆ SFO         ┆ San Francisco ┆ San Francisco ┆ 13390   │
│        ┆ International  ┆                ┆             ┆ International ┆               ┆         │
│        ┆ Airp…          ┆                ┆             ┆ Ai…           ┆               ┆         │
│ OGG    ┆ Kahului        ┆ Kahului        ┆ HNL         ┆ Daniel K      ┆ Honolulu,     ┆ 12383   │
│        ┆ International  ┆                ┆             ┆ Inouye        ┆ Oahu          ┆         │
│        ┆ Airport        ┆                ┆             ┆ International ┆               ┆         │
│        ┆                ┆                ┆             ┆ …             ┆               ┆         │
│ LGA    ┆ LaGuardia      ┆ New York       ┆ BOS         ┆ Logan         ┆ Boston        ┆ 12035   │
│        ┆ Airport        ┆                ┆             ┆ International ┆               ┆         │
│        ┆                ┆                ┆             ┆ Airport       ┆               ┆         │
│ BOS    ┆ Logan          ┆ Boston         ┆ LGA         ┆ LaGuardia     ┆ New York      ┆ 12029   │
│        ┆ International  ┆                ┆             ┆ Airport       ┆               ┆         │
│        ┆ Airport        ┆                ┆             ┆               ┆               ┆         │
│ HNL    ┆ Daniel K       ┆ Honolulu, Oahu ┆ OGG         ┆ Kahului       ┆ Kahului       ┆ 12014   │
│        ┆ Inouye         ┆                ┆             ┆ International ┆               ┆         │
│        ┆ International  ┆                ┆             ┆ Airport       ┆               ┆         │
│        ┆ …              ┆                ┆             ┆               ┆               ┆         │
│ LAX    ┆ Los Angeles    ┆ Los Angeles    ┆ LAS         ┆ Harry Reid    ┆ Las Vegas     ┆ 11773   │
│        ┆ International  ┆                ┆             ┆ International ┆               ┆         │
│        ┆ Airp…          ┆                ┆             ┆ Airpo…        ┆               ┆         │
│ LAS    ┆ Harry Reid     ┆ Las Vegas      ┆ LAX         ┆ Los Angeles   ┆ Los Angeles   ┆ 11729   │
│        ┆ International  ┆                ┆             ┆ International ┆               ┆         │
│        ┆ Airpo…         ┆                ┆             ┆ Airp…         ┆               ┆         │
│ LAX    ┆ Los Angeles    ┆ Los Angeles    ┆ SAN         ┆ San Diego     ┆ San Diego     ┆ 11257   │
│        ┆ International  ┆                ┆             ┆ International ┆               ┆         │
│        ┆ Airp…          ┆                ┆             ┆ Airpor…       ┆               ┆         │
│ SAN    ┆ San Diego      ┆ San Diego      ┆ LAX         ┆ Los Angeles   ┆ Los Angeles   ┆ 11224   │
│        ┆ International  ┆                ┆             ┆ International ┆               ┆         │
│        ┆ Airpor…        ┆                ┆             ┆ Airp…         ┆               ┆         │
└────────┴────────────────┴────────────────┴─────────────┴───────────────┴───────────────┴─────────┘

In [23]:
num_bars = 30

alt.Chart(
    flights_info_us.sort('flights', descending=True).select(
        (pl.col('origin') + " to " + pl.col('destination')).alias('flight'),
        pl.col('origin'),
        pl.col('origin_name'),
        pl.col('origin_municipality'),
        pl.col('destination'),
        pl.col('dest_name'),
        pl.col('dest_municipality'),
        pl.col('flights'),
    ).head(num_bars),
    title=f'most frequent flights (u.s.) - top {num_bars}'
).transform_calculate(
    custom_tooltip='datum.origin_name + " (" + datum.origin_municipality + ") " + " to " + datum.dest_name + " (" + datum.dest_municipality + ")"',
).mark_bar(
    color='#f9ebc0',
    opacity=0.75,
    stroke='black',
).encode(
    x=alt.X('flights:Q', title='number of flights'),
    y=alt.Y('flight:N', title='', sort=alt.SortField('flights', order='descending')),
    tooltip='custom_tooltip:N',
).properties(
    width=800,
    height=700,
)

alt.Chart(...)